In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/bdd100k-weather-classification/val/unknown/c0a7a9dc-497459f0.jpg
/kaggle/input/bdd100k-weather-classification/val/unknown/c9dc96aa-01dec7af.jpg
/kaggle/input/bdd100k-weather-classification/val/unknown/c6a4abc9-8897c0c0.jpg
/kaggle/input/bdd100k-weather-classification/val/unknown/b52e3ad8-aebd0e55.jpg
/kaggle/input/bdd100k-weather-classification/val/unknown/c51de804-7b18411f.jpg
/kaggle/input/bdd100k-weather-classification/val/unknown/c4f4718b-7a18cd62.jpg
/kaggle/input/bdd100k-weather-classification/val/unknown/c8a8a8b3-8f839ecb.jpg
/kaggle/input/bdd100k-weather-classification/val/unknown/c47ac0cd-42edbc96.jpg
/kaggle/input/bdd100k-weather-classification/val/unknown/c088650e-f71b7011.jpg
/kaggle/input/bdd100k-weather-classification/val/unknown/b25fd5d3-fa4bfca0.jpg
/kaggle/input/bdd100k-weather-classification/val/unknown/b499ff48-6a0b212e.jpg
/kaggle/input/bdd100k-weather-classification/val/unknown/b9d12c48-d855b440.jpg
/kaggle/input/bdd100k-weather-classification/val/unk

In [2]:
import os, random
from glob import glob
from PIL import Image
import torch
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms

device = "cuda" if torch.cuda.is_available() else "cpu"

DATA_DIR = "/kaggle/input/bdd100k-weather-classification/train"

TARGET_CLASSES = {
    "partly cloudy": "partly cloudy",   # SOURCE domain
    "clear": "clear"   # TARGET domain
}

LIMIT = 700  # take only 700 images per class

# Collect image paths
snow_imgs = sorted(glob(os.path.join(DATA_DIR, "partly cloudy", "*.jpg")))
clear_imgs = sorted(glob(os.path.join(DATA_DIR, "clear", "*.jpg")))

random.shuffle(snow_imgs)
random.shuffle(clear_imgs)

snow_imgs = snow_imgs[:LIMIT]
clear_imgs = clear_imgs[:LIMIT]

print("partly cloudy images:", len(snow_imgs))
print("Clear images:", len(clear_imgs))


partly cloudy images: 700
Clear images: 700


In [3]:
class WeatherDataset(Dataset):
    def __init__(self, img_list, img_size=128):
        self.paths = img_list
        self.transform = transforms.Compose([
            transforms.Resize((img_size, img_size)),
            transforms.RandomHorizontalFlip(0.5),
            transforms.ToTensor(),
            transforms.Normalize((0.5,)*3, (0.5,)*3),
        ])

    def __len__(self):
        return len(self.paths)

    def __getitem__(self, idx):
        img = Image.open(self.paths[idx]).convert("RGB")
        return self.transform(img)


In [4]:
IMG_SIZE = 128
BATCH_SIZE = 1

dsA = WeatherDataset(snow_imgs, IMG_SIZE)   # Snow → Clear
dsB = WeatherDataset(clear_imgs, IMG_SIZE)

dlA = DataLoader(dsA, batch_size=BATCH_SIZE, shuffle=True)
dlB = DataLoader(dsB, batch_size=BATCH_SIZE, shuffle=True)

print("✅ Dataset Ready")


✅ Dataset Ready


In [5]:
import torch.nn as nn
import itertools

# --- ResNet Block ---
class ResBlock(nn.Module):
    def __init__(self, dim):
        super().__init__()
        self.block = nn.Sequential(
            nn.ReflectionPad2d(1),
            nn.Conv2d(dim, dim, 3),
            nn.InstanceNorm2d(dim),
            nn.ReLU(True),
            nn.ReflectionPad2d(1),
            nn.Conv2d(dim, dim, 3),
            nn.InstanceNorm2d(dim)
        )
    def forward(self, x): return x + self.block(x)

# --- Generator ---
class Generator(nn.Module):
    def __init__(self, in_c=3, out_c=3, n_blocks=6):
        super().__init__()
        m = [
            nn.ReflectionPad2d(3),
            nn.Conv2d(in_c, 64, 7),
            nn.InstanceNorm2d(64),
            nn.ReLU(True),

            nn.Conv2d(64,128,3,2,1),
            nn.InstanceNorm2d(128),
            nn.ReLU(True),

            nn.Conv2d(128,256,3,2,1),
            nn.InstanceNorm2d(256),
            nn.ReLU(True),
        ]
        for _ in range(n_blocks): m.append(ResBlock(256))
        m += [
            nn.ConvTranspose2d(256,128,3,2,1,1),
            nn.InstanceNorm2d(128),
            nn.ReLU(True),

            nn.ConvTranspose2d(128,64,3,2,1,1),
            nn.InstanceNorm2d(64),
            nn.ReLU(True),

            nn.ReflectionPad2d(3),
            nn.Conv2d(64,out_c,7),
            nn.Tanh()
        ]
        self.model = nn.Sequential(*m)

    def forward(self,x): return self.model(x)

# --- PatchGAN ---
class Discriminator(nn.Module):
    def __init__(self, in_c=3):
        super().__init__()
        def block(i,o,normalize=True):
            layers=[nn.Conv2d(i,o,4,2,1)]
            if normalize: layers += [nn.InstanceNorm2d(o)]
            layers += [nn.LeakyReLU(0.2,True)]
            return layers
        self.model = nn.Sequential(
            *block(3,64,False),
            *block(64,128),
            *block(128,256),
            nn.Conv2d(256,1,4,1,1)
        )
    def forward(self,x): return self.model(x)


In [6]:
G_AB = Generator().to(device)  # Snow → Clear
G_BA = Generator().to(device)  # Clear → Snow
D_A = Discriminator().to(device)
D_B = Discriminator().to(device)

criterion_gan = nn.MSELoss()
criterion_cycle = nn.L1Loss()
criterion_id = nn.L1Loss()

optimizer_G = torch.optim.Adam(
    itertools.chain(G_AB.parameters(), G_BA.parameters()),
    lr=2e-4, betas=(0.5,0.999)
)

optimizer_D = torch.optim.Adam(
    itertools.chain(D_A.parameters(), D_B.parameters()),
    lr=2e-4, betas=(0.5,0.999)
)


In [7]:
!pip install pytorch-fid --quiet


In [8]:
import torch
torch.cuda.is_available(), torch.cuda.get_device_name(0)


(True, 'Tesla T4')

In [9]:
from tqdm import tqdm

def denorm(x): return (x * 0.5) + 0.5

EPOCHS = 20

for epoch in range(1, EPOCHS+1):
    for real_A, real_B in tqdm(zip(dlA, dlB), total=min(len(dlA),len(dlB))):
        real_A, real_B = real_A.to(device), real_B.to(device)
        valid = torch.ones_like(D_A(real_A))
        fake = torch.zeros_like(valid)

        # --- Train Generators ---
        optimizer_G.zero_grad()

        fake_B = G_AB(real_A)
        fake_A = G_BA(real_B)

        loss_id = criterion_id(G_BA(real_A), real_A) + criterion_id(G_AB(real_B), real_B)

        loss_gan = criterion_gan(D_B(fake_B), valid) + criterion_gan(D_A(fake_A), valid)

        rec_A = G_BA(fake_B)
        rec_B = G_AB(fake_A)
        loss_cycle = criterion_cycle(rec_A, real_A)*10 + criterion_cycle(rec_B, real_B)*10

        loss_G = loss_id*0.5 + loss_gan + loss_cycle
        loss_G.backward()
        optimizer_G.step()

        # --- Train Discriminators ---
        optimizer_D.zero_grad()

        loss_D_A = (criterion_gan(D_A(real_A), valid) + criterion_gan(D_A(fake_A.detach()), fake))*0.5
        loss_D_B = (criterion_gan(D_B(real_B), valid) + criterion_gan(D_B(fake_B.detach()), fake))*0.5

        (loss_D_A + loss_D_B).backward()
        optimizer_D.step()

    print(f"Epoch {epoch} | G:{loss_G:.3f} D:{(loss_D_A+loss_D_B):.3f}")


100%|██████████| 700/700 [01:35<00:00,  7.30it/s]


Epoch 1 | G:5.864 D:0.459


100%|██████████| 700/700 [01:41<00:00,  6.90it/s]


Epoch 2 | G:4.640 D:0.497


100%|██████████| 700/700 [01:41<00:00,  6.90it/s]


...

Epoch 18 | G:3.874 D:0.451


100%|██████████| 700/700 [01:41<00:00,  6.91it/s]


Epoch 19 | G:2.951 D:0.449


100%|██████████| 700/700 [01:41<00:00,  6.89it/s]

Epoch 20 | G:2.875 D:0.231


In [10]:
# Save full models
torch.save(G_AB, "/kaggle/working/G_AB_full_partlycloudy_to_clear.pth")
torch.save(G_BA, "/kaggle/working/G_BA_full_clear_to_partlycloudy.pth")

# Also save weights (backup)
torch.save(G_AB.state_dict(), "/kaggle/working/G_AB_partlycloudy_to_clear.pth")
torch.save(G_BA.state_dict(), "/kaggle/working/G_BA_clear_to_partlycloudy.pth")

print("✅ Models saved!")


✅ Models saved!


In [11]:
import json

json.dump(snow_imgs, open("/kaggle/working/test_partlycloudy_files.json", "w"))
json.dump(clear_imgs, open("/kaggle/working/test_clear_files.json", "w"))

print("✅ Test file lists saved")


✅ Test file lists saved
